In [1]:
import numpy as np
import pandas as pd

import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objects as go


from time import time
import numpy as np
import matplotlib.path as mpltPath

import math

import warnings
warnings.filterwarnings('ignore')

In [2]:
folder="/home/shankar/All_thesis/Thesis_program/Data/shawnee/location_1/Kmeans"

In [3]:
location_in_time=pd.read_csv(folder+"/location_in_time.csv")

In [4]:
location_in_time

Unnamed: 0                     Start                       End  passID  \
0           0  2023-01-16T17:24:39.000Z  2023-01-16T17:25:25.000Z     115   
1           1  2023-01-16T17:25:52.000Z  2023-01-16T17:26:38.000Z     117   
2           2  2023-01-16T17:27:08.000Z  2023-01-16T17:27:55.000Z     118   
3           3  2023-01-16T17:29:06.000Z  2023-01-16T17:29:53.000Z     120   
4           4  2023-01-16T17:30:23.000Z  2023-01-16T17:31:09.000Z     121   

     lat_min    lat_max   long_min   long_max  
0  35.670006  35.670785 -96.662316 -96.662305  
1  35.670014  35.670792 -96.662317 -96.662304  
2  35.670003  35.670800 -96.662341 -96.662327  
3  35.670000  35.670794 -96.662342 -96.662329  
4  35.670007  35.670784 -96.662333 -96.662319

In [5]:
passes=location_in_time["passID"].values
passes

array([115, 117, 118, 120, 121])

In [6]:
each_data=[pd.read_csv(folder+f"/cluster_predicted_pass_{x}.csv") for x in location_in_time["passID"]]

In [7]:
# Compute heading
def compute_heading(df):
    df["heading"] = 0
    for i in range(len(df) - 1):
        a = df.loc[i, "latitude"] - df.loc[i + 1, "latitude"]
        b = df.loc[i, "longitude"] - df.loc[i + 1, "longitude"]
        d = 180 / np.pi * np.arctan2(a, b) + 180
        df.loc[i, "heading"] = d

In [8]:
def projectRollerWidth(df_in, rollerWidth=6, nPoints=6):
    df=df_in.copy(deep=True)
    copyDF = df.copy()
    halfWidth = rollerWidth // 2
    for i in np.arange(-halfWidth, halfWidth, rollerWidth / nPoints):
        tmpDF = copyDF.copy()
        tmpDF.latitude = (
            np.sin(2 * np.pi / 360 * (copyDF.heading.values - 90)) * i / 3600 / 101
            + copyDF.latitude.values
        )
        tmpDF.longitude = (
            np.cos(2 * np.pi / 360 * (copyDF.heading.values - 90)) * i / 3600 / 80
            + copyDF.longitude.values
        )
        tmpDF.original = False
        df = df.append(tmpDF)
    df =df.sort_values("timestamp")
    return df

In [9]:
each_data_projected=[[]]*len(each_data)
for i in range(len(passes)):
    each_data[i]["pass_no"]=i
    length=len(each_data[i])
    latitudes = np.linspace(location_in_time["lat_min"][i],location_in_time["lat_max"][i] , num=length)
    print(len(latitudes))
    each_data[i]["latitude"]=latitudes
    longitudes= np.linspace(location_in_time["long_min"][i],location_in_time["long_max"][i] , num=length)
    each_data[i]["longitude"]=longitudes
    
    each_data[i]["prev"]=each_data[i]["cluster"].shift(1)
    each_data[i]["change"]=each_data[i].apply(lambda x: 1 if abs(x["prev"]-x["cluster"]>1)  else 0, axis=1)
       
    print(i)
    if i==0:
        each_data[i]["first"]=True
        each_data[i]["last"]=False
    elif i==len(passes)-1:
        each_data[i]["first"]=False
        each_data[i]["last"]=True
    else:
        each_data[i]["first"]=False
        each_data[i]["last"]=False
        
        
    compute_heading(each_data[i])
    each_data_projected[i]=projectRollerWidth(each_data[i])

        
full_data=pd.concat(each_data)
full_data=full_data[full_data["pass_no"]!=0]

full_data_projected=pd.concat(each_data_projected)
full_data_projected=full_data_projected[full_data_projected["pass_no"]!=0]

358
0
360
1
366
2
366
3
360
4


In [10]:
full_data["time"]=full_data["timestamp"]
full_data["passID"]=full_data["pass_no"]
full_data["speed"]=1.1
full_data["temperature"]=167.5

full_data["density"]=full_data["cluster"]
full_data.to_csv(folder+"/full_data_to_project.csv")
full_data

Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
1               1           1  2023-01-16 17:25:52.257000+00:00    82.183425   
2               2           2  2023-01-16 17:25:52.384000+00:00    83.212034   
3               3           3  2023-01-16 17:25:52.511000+00:00    58.360112   
4               4           4  2023-01-16 17:25:52.638000+00:00    62.575446   
..            ...         ...                               ...          ...   
355           355         355  2023-01-16 17:31:08.215000+00:00    18.406951   
356           356         356  2023-01-16 17:31:08.342000+00:00    67.584552   
357           357         357  2023-01-16 17:31:08.469000+00:00    82.175854   
358           358         358  2023-01-16 17:31:08.596000+00:00   100.000000   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   

           p0        p1        p2        p3        p4        p5  ...  prev  \
0   -2.000000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
1   -2.000000 -0.085897 -0.100313  0.562901  1.384732  0.605973  ...   4.0   
2   -2.000000  0.909739 -0.090134  0.542970  0.487589  0.860677  ...   3.0   
3   -0.510243 -0.707589 -0.276745 -0.355957 -0.028058  0.654395  ...   0.0   
4    0.922105 -0.875624 -0.435802  0.125723 -0.576983  0.532818  ...   2.0   
..        ...       ...       ...       ...       ...       ...  ...   ...   
355  0.619154  2.000000 -0.067383 -0.711903 -0.299709 -0.395371  ...   4.0   
356  0.658804  0.218019 -0.212631 -0.182176  1.719183  1.880953  ...   2.0   
357  0.966712  0.201359  0.004933  2.000000  0.814174 -0.509651  ...   4.0   
358  1.250349 -0.648439  1.299200  2.000000 -0.037076 -0.079023  ...   3.0   
359  1.158490 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   

     change  first   last    heading                              time  \
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
1         0  False  False  89.042705  2023-01-16 17:25:52.257000+00:00   
2         1  False  False  89.042705  2023-01-16 17:25:52.384000+00:00   
3         0  False  False  89.042705  2023-01-16 17:25:52.511000+00:00   
4         0  False  False  89.042705  2023-01-16 17:25:52.638000+00:00   
..      ...    ...    ...        ...                               ...   
355       1  False   True  88.967755  2023-01-16 17:31:08.215000+00:00   
356       0  False   True  88.967755  2023-01-16 17:31:08.342000+00:00   
357       0  False   True  88.967755  2023-01-16 17:31:08.469000+00:00   
358       0  False   True  88.967755  2023-01-16 17:31:08.596000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   

     passID  speed  temperature  density  
0         1    1.1        167.5        4  
1         1    1.1        167.5        3  
2         1    1.1        167.5        0  
3         1    1.1        167.5        2  
4         1    1.1        167.5        2  
..      ...    ...          ...      ...  
355       4    1.1        167.5        2  
356       4    1.1        167.5        4  
357       4    1.1        167.5        3  
358       4    1.1        167.5        3  
359       4    1.1        167.5        2  

[1452 rows x 25 columns]

In [11]:
full_data_projected["time"]=full_data_projected["timestamp"]
full_data_projected["passID"]=full_data_projected["pass_no"]

full_data_projected["speed"]=1.1
full_data_projected["temperature"]=167.5

full_data_projected["density"]=full_data_projected["cluster"]
full_data_projected

# full_data_projected.to_csv(folder+"full_data_projected.csv")

Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
0               0           0  2023-01-16 17:25:52.120000+00:00   100.000000   
..            ...         ...                               ...          ...   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   
359           359         359  2023-01-16 17:31:08.723000+00:00    38.006939   

          p0        p1        p2        p3        p4        p5  ...  prev  \
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
0   -2.00000  2.000000  2.000000  0.935329  2.000000  2.000000  ...   NaN   
..       ...       ...       ...       ...       ...       ...  ...   ...   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   
359  1.15849 -0.567994  0.230944  0.437043 -0.654288  0.330046  ...   3.0   

     change  first   last    heading                              time  \
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
0         0  False  False  89.042705  2023-01-16 17:25:52.120000+00:00   
..      ...    ...    ...        ...                               ...   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   
359       0  False   True   0.000000  2023-01-16 17:31:08.723000+00:00   

     passID  speed  temperature  density  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
0         1    1.1        167.5        4  
..      ...    ...          ...      ...  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  
359       4    1.1        167.5        2  

[10164 rows x 25 columns]

In [12]:
lon_min = full_data_projected.longitude.min()
lon_max = full_data_projected.longitude.max()
lat_min = full_data_projected.longitude.min()
lat_max = full_data_projected.longitude.max()

nHexBins_lat = int(
    (lat_max - lat_min) * 3600 * 80 / 2
)  
nHexBins_lon = int(
    (lon_max - lon_min) * 3600 * 80 / 2
    
)  

nHexBins=max(nHexBins_lon,nHexBins_lat)
nHexBins

7

In [13]:
def getLastValue(hexBin):
#     print (hexBin)
    return hexBin[-1]


coverageFig = {}
# Coverage map colored by pass count
coverageFig["passes"] = ff.create_hexbin_mapbox(
    data_frame=full_data_projected,
    lat="latitude",
    lon="longitude",
    labels={"color": "Number of Passes"},
    nx_hexagon=nHexBins,
    agg_func=getLastValue,
    show_original_data=True,
    color="density",
    zoom=18,
)

coverageFig

{'passes': Figure({
     'data': [{'coloraxis': 'coloraxis',
               'customdata': array([[4.0, '-1.6870763123695685,0.6671710130044681', 0],
                                    [3.0, '-1.6870763123695685,0.6671712519187004', 0],
                                    [0.0, '-1.6870763123695685,0.6671714908329327', 0],
                                    ...,
                                    [2.0, '-1.6870754157777923,0.667187617543613', 0],
                                    [0.0, '-1.6870754157777923,0.6671878564578453', 0],
                                    [4.0, '-1.6870754157777923,0.6671880953720776', 0]], dtype=object),
               'geojson': {'features': [{'geometry': {'coordinates': [[[-
                                                                      96.66235241527
                                                                      079, 35.669994
                                                                      47324763], [-
                           

In [14]:
len(coverageFig["passes"].data[0].geojson["features"]), len(coverageFig["passes"].data[0].customdata)

(1103, 906)

In [15]:
vertices_list_c=[coverageFig["passes"].data[0].geojson["features"][i]["geometry"]['coordinates'][0] 
                 for i in range (len(coverageFig["passes"].data[0].geojson["features"]))]
vertices_collection={coverageFig["passes"].data[0].geojson["features"][i]["id"]:
                      coverageFig["passes"].data[0].geojson["features"][i]["geometry"]['coordinates'][0]
                     for i in range (len(coverageFig["passes"].data[0].geojson["features"]))}

len(vertices_collection)

1103

In [16]:
def get_data_inside(dataframe,vertices):
#     print(vertices_k_v)
    vertex_path=mpltPath.Path(vertices)
    ret_data = vertex_path.contains_points(np.array(dataframe[["longitude","latitude"]]))
    if not dataframe[ret_data].empty:
#         print(dataframe[ret_data])
        return dataframe[ret_data]
    
get_data={vertex_point: get_data_inside(full_data_projected,vertices_collection[vertex_point])
          for vertex_point in vertices_collection}

In [17]:
def get_pass_and_density(df):
    try:
        return df.groupby(["passID","density"]).size() 
    except:
        return None

final_data={vertex_point: get_pass_and_density(get_data[vertex_point]) for vertex_point in get_data}

In [18]:
list(final_data.values())[68]

In [49]:
with_val=([x for x in get_data.values() if x is not None])
with_val[789]

Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
343           343         343  2023-01-16 17:26:35.691000+00:00    24.427236   
344           344         344  2023-01-16 17:26:35.818000+00:00    33.365076   
345           345         345  2023-01-16 17:26:35.945000+00:00    37.248666   
346           346         346  2023-01-16 17:27:52.319000+00:00    66.170731   
347           347         347  2023-01-16 17:27:52.446000+00:00    62.013504   
347           347         347  2023-01-16 17:31:07.199000+00:00    18.508862   
347           347         347  2023-01-16 17:31:07.199000+00:00    18.508862   
347           347         347  2023-01-16 17:31:07.199000+00:00    18.508862   
348           348         348  2023-01-16 17:31:07.326000+00:00    75.503528   
348           348         348  2023-01-16 17:31:07.326000+00:00    75.503528   
348           348         348  2023-01-16 17:31:07.326000+00:00    75.503528   
349           349         349  2023-01-16 17:31:07.453000+00:00   100.000000   
349           349         349  2023-01-16 17:31:07.453000+00:00   100.000000   
349           349         349  2023-01-16 17:31:07.453000+00:00   100.000000   

           p0        p1        p2        p3        p4        p5  ...  prev  \
343  0.134194  0.481138 -0.334519 -0.680171 -0.870799 -0.807278  ...   2.0   
344  0.491639 -0.122989  2.000000 -0.496999 -0.873280 -0.995393  ...   1.0   
345  0.444727 -1.116315  1.650396 -0.554784 -0.947448 -0.050438  ...   1.0   
346  0.041104  0.548169 -0.816278 -0.004505 -0.231564  1.360373  ...   1.0   
347  0.460591  1.735161 -0.702873 -0.151633  0.522208  0.255639  ...   2.0   
347  0.529506 -0.308274 -0.455989 -0.356230  0.386935 -1.018323  ...   3.0   
347  0.529506 -0.308274 -0.455989 -0.356230  0.386935 -1.018323  ...   3.0   
347  0.529506 -0.308274 -0.455989 -0.356230  0.386935 -1.018323  ...   3.0   
348  0.790196  2.000000  0.404745  0.181737  2.000000  0.332894  ...   2.0   
348  0.790196  2.000000  0.404745  0.181737  2.000000  0.332894  ...   2.0   
348  0.790196  2.000000  0.404745  0.181737  2.000000  0.332894  ...   2.0   
349  1.637877  1.978705 -0.318987  2.000000  1.536730 -0.072775  ...   4.0   
349  1.637877  1.978705 -0.318987  2.000000  1.536730 -0.072775  ...   4.0   
349  1.637877  1.978705 -0.318987  2.000000  1.536730 -0.072775  ...   4.0   

     change  first   last    heading                              time  \
343       0  False  False  89.042705  2023-01-16 17:26:35.691000+00:00   
344       0  False  False  89.042705  2023-01-16 17:26:35.818000+00:00   
345       0  False  False  89.042705  2023-01-16 17:26:35.945000+00:00   
346       0  False  False  88.993653  2023-01-16 17:27:52.319000+00:00   
347       0  False  False  88.993653  2023-01-16 17:27:52.446000+00:00   
347       0  False   True  88.967755  2023-01-16 17:31:07.199000+00:00   
347       0  False   True  88.967755  2023-01-16 17:31:07.199000+00:00   
347       0  False   True  88.967755  2023-01-16 17:31:07.199000+00:00   
348       0  False   True  88.967755  2023-01-16 17:31:07.326000+00:00   
348       0  False   True  88.967755  2023-01-16 17:31:07.326000+00:00   
348       0  False   True  88.967755  2023-01-16 17:31:07.326000+00:00   
349       0  False   True  88.967755  2023-01-16 17:31:07.453000+00:00   
349       0  False   True  88.967755  2023-01-16 17:31:07.453000+00:00   
349       0  False   True  88.967755  2023-01-16 17:31:07.453000+00:00   

     passID  speed  temperature  density  
343       1    1.1        167.5        1  
344       1    1.1        167.5        1  
345       1    1.1        167.5        2  
346       2    1.1        167.5        2  
347       2    1.1        167.5        4  
347       4    1.1        167.5        2  
347       4    1.1        167.5        2  
347       4    1.1        167.5        2  
348       4    1.1        167.5        4  
348       4    1.1        167.5        4  
348       4    1.1        167.5        4  
349   

In [31]:
with_val[789].drop_duplicates(subset = "time")

Unnamed: 0.1  Unnamed: 0                         timestamp  total_power  \
343           343         343  2023-01-16 17:26:35.691000+00:00    24.427236   
344           344         344  2023-01-16 17:26:35.818000+00:00    33.365076   
345           345         345  2023-01-16 17:26:35.945000+00:00    37.248666   
346           346         346  2023-01-16 17:27:52.319000+00:00    66.170731   
347           347         347  2023-01-16 17:27:52.446000+00:00    62.013504   
347           347         347  2023-01-16 17:31:07.199000+00:00    18.508862   
348           348         348  2023-01-16 17:31:07.326000+00:00    75.503528   
349           349         349  2023-01-16 17:31:07.453000+00:00   100.000000   

           p0        p1        p2        p3        p4        p5  ...  prev  \
343  0.134194  0.481138 -0.334519 -0.680171 -0.870799 -0.807278  ...   2.0   
344  0.491639 -0.122989  2.000000 -0.496999 -0.873280 -0.995393  ...   1.0   
345  0.444727 -1.116315  1.650396 -0.554784 -0.947448 -0.050438  ...   1.0   
346  0.041104  0.548169 -0.816278 -0.004505 -0.231564  1.360373  ...   1.0   
347  0.460591  1.735161 -0.702873 -0.151633  0.522208  0.255639  ...   2.0   
347  0.529506 -0.308274 -0.455989 -0.356230  0.386935 -1.018323  ...   3.0   
348  0.790196  2.000000  0.404745  0.181737  2.000000  0.332894  ...   2.0   
349  1.637877  1.978705 -0.318987  2.000000  1.536730 -0.072775  ...   4.0   

     change  first   last    heading                              time  \
343       0  False  False  89.042705  2023-01-16 17:26:35.691000+00:00   
344       0  False  False  89.042705  2023-01-16 17:26:35.818000+00:00   
345       0  False  False  89.042705  2023-01-16 17:26:35.945000+00:00   
346       0  False  False  88.993653  2023-01-16 17:27:52.319000+00:00   
347       0  False  False  88.993653  2023-01-16 17:27:52.446000+00:00   
347       0  False   True  88.967755  2023-01-16 17:31:07.199000+00:00   
348       0  False   True  88.967755  2023-01-16 17:31:07.326000+00:00   
349       0  False   True  88.967755  2023-01-16 17:31:07.453000+00:00   

     passID  speed  temperature  density  
343       1    1.1        167.5        1  
344       1    1.1        167.5        1  
345       1    1.1        167.5        2  
346       2    1.1        167.5        2  
347       2    1.1        167.5        4  
347       4    1.1        167.5        2  
348       4    1.1        167.5        4  
349       4    1.1        167.5        4  

[8 rows x 25 columns]

In [25]:
def get_avg_density_per_pass(df):
    try:
        return df.drop_duplicates(subset = "time").groupby(["passID"])["density"].mean() 
    except:
        return None

pass_dens={vertex_point: get_avg_density_per_pass(get_data[vertex_point]) for vertex_point in get_data}
pass_dens_with_val=([x for x in pass_dens.values() if x is not None])


In [48]:
pass_dens_with_val[789]

passID
1    1.333333
2    3.000000
4    3.333333
Name: density, dtype: float64

In [77]:
new_z=[[list(pass_dens_with_val[i]),list(pass_dens_with_val[i].index)] for i in range(len(pass_dens_with_val))]
new_z

[[[4.0], [3]],
 [[0.0, 2.3333333333333335], [2, 3]],
 [[2.3333333333333335, 0.0], [2, 3]],
 [[2.0, 0.5], [2, 3]],
 [[1.3333333333333333, 0.5], [2, 3]],
 [[1.6666666666666667, 0.3333333333333333], [2, 3]],
 [[1.5, 2.3333333333333335], [2, 3]],
 [[1.0, 0.6666666666666666], [2, 3]],
 [[2.0, 0.6666666666666666], [2, 3]],
 [[1.0, 1.3333333333333333], [2, 3]],
 [[2.5, 1.0], [2, 3]],
 [[1.5, 1.5], [2, 3]],
 [[1.5, 0.5], [2, 3]],
 [[3.0, 2.0], [2, 3]],
 [[1.0, 0.5], [2, 3]],
 [[3.0, 1.0], [2, 3]],
 [[1.0], [3]],
 [[2.3333333333333335], [3]],
 [[1.0], [3]],
 [[0.5], [3]],
 [[0.0], [3]],
 [[1.5], [3]],
 [[4.0], [3]],
 [[0.0, 2.3333333333333335, 1.3333333333333333], [2, 3, 4]],
 [[2.3333333333333335, 0.0, 2.6666666666666665], [2, 3, 4]],
 [[2.0, 0.5, 4.0], [2, 3, 4]],
 [[1.3333333333333333, 0.5, 3.0], [2, 3, 4]],
 [[1.6666666666666667, 0.3333333333333333, 4.0], [2, 3, 4]],
 [[1.3333333333333333, 2.3333333333333335, 3.5], [2, 3, 4]],
 [[1.0, 0.6666666666666666, 3.3333333333333335], [2, 3, 4]],
 [[

In [51]:
# coverageFig["passes"].data[0].geojson["features"][i]["geometry"]['coordinates'][0]
coverageFig

{'passes': Figure({
     'data': [{'coloraxis': 'coloraxis',
               'customdata': array([[4.0, '-1.6870763123695685,0.6671710130044681', 0],
                                    [3.0, '-1.6870763123695685,0.6671712519187004', 0],
                                    [0.0, '-1.6870763123695685,0.6671714908329327', 0],
                                    ...,
                                    [2.0, '-1.6870754157777923,0.667187617543613', 0],
                                    [0.0, '-1.6870754157777923,0.6671878564578453', 0],
                                    [4.0, '-1.6870754157777923,0.6671880953720776', 0]], dtype=object),
               'geojson': {'features': [{'geometry': {'coordinates': [[[-
                                                                      96.66235241527
                                                                      079, 35.669994
                                                                      47324763], [-
                           

In [81]:
coverageFig["passes"].data[0].z=new_z
coverageFig

{'passes': Figure({
     'data': [{'coloraxis': 'coloraxis',
               'customdata': array([[4.0, '-1.6870763123695685,0.6671710130044681', 0],
                                    [3.0, '-1.6870763123695685,0.6671712519187004', 0],
                                    [0.0, '-1.6870763123695685,0.6671714908329327', 0],
                                    ...,
                                    [2.0, '-1.6870754157777923,0.667187617543613', 0],
                                    [0.0, '-1.6870754157777923,0.6671878564578453', 0],
                                    [4.0, '-1.6870754157777923,0.6671880953720776', 0]], dtype=object),
               'geojson': {'features': [{'geometry': {'coordinates': [[[-
                                                                      96.66235241527
                                                                      079, 35.669994
                                                                      47324763], [-
                           